## <center> Choropleth for the petition "Do Not Prorogue Parliament"</center>

Read and process petition data downloaded from the [https://petition.parliament.uk/petitions/269157](https://petition.parliament.uk/petitions/269157)

In [1]:
import numpy as np
import pandas as pd
import json
import geopandas as gpd
from shapely.geometry import LineString, MultiLineString
import plotly.graph_objects as go
import plotly.io as pio

In [2]:
pio.templates.default = "none"

In [4]:
import urllib.request

url = "https://petition.parliament.uk/petitions/269157.json"

with urllib.request.urlopen(url) as url:
    jdata = json.loads(url.read().decode())
    

In [5]:
jdata.keys()

dict_keys(['links', 'data'])

In [6]:
signatures = jdata['data']['attributes']['signature_count']
signatures

1695178

In [7]:
jdata['data']['attributes']['signatures_by_constituency'][0]

{'name': 'Edinburgh East',
 'ons_code': 'S14000022',
 'mp': 'Tommy Sheppard MP',
 'signature_count': 6014}

Create a `pandas.DataFrame` from petition data:

In [8]:
d = {'name': [],
     'ons_code': [],
     'mp': [],
     'signature_count': []
}
for attr in jdata['data']['attributes']['signatures_by_constituency']:
    d['name'].append(attr['name'])
    d['ons_code'].append(attr['ons_code'])
    d['mp'].append(attr['mp'])
    d['signature_count'].append(attr['signature_count'])

dfpt = pd.DataFrame(d)
dfpt.head()

name   ons_code                    mp  signature_count
0             Edinburgh East  S14000022     Tommy Sheppard MP             6014
1  Edinburgh North and Leith  S14000023       Deidre Brock MP             9012
2            Edinburgh South  S14000024         Ian Murray MP             6847
3       Edinburgh South West  S14000025   Joanna Cherry QC MP             5177
4             Edinburgh West  S14000026  Christine Jardine MP             4241

Read a csv file giving information on electorate in each constituency:

In [9]:
dfe = pd.read_csv('https://raw.githubusercontent.com/TTitcombe/ConstituencyMap/master/data/map/ge2015_electorate.csv')
dfe.head()

constituency_name  electorate
0            Aberavon       49821
1           Aberconwy       45525
2      Aberdeen North       67745
3      Aberdeen South       68056
4  Airdrie and Shotts       66792

In [10]:
len(dfpt), len(dfe)

(650, 650)

In [11]:
dfpt.sort_values(['name'], inplace=True)
dfpt.head()

name   ons_code                  mp  signature_count
42             Aberavon  W07000049  Stephen Kinnock MP              779
43            Aberconwy  W07000058        Guto Bebb MP             1399
16       Aberdeen North  S14000001  Kirsty Blackman MP             2137
25       Aberdeen South  S14000002     Ross Thomson MP             2727
355  Airdrie and Shotts  S14000003        Neil Gray MP             1198

In [12]:
constituencyn  = list(dfe['constituency_name'])

name = list(dfpt['name'])
np.where(name != constituencyn)

(array([0], dtype=int64),)

In [13]:
list(zip(name, constituencyn))[0:10]

[('Aberavon', 'Aberavon'),
 ('Aberconwy', 'Aberconwy'),
 ('Aberdeen North', 'Aberdeen North'),
 ('Aberdeen South', 'Aberdeen South'),
 ('Airdrie and Shotts', 'Airdrie and Shotts'),
 ('Aldershot', 'Aldershot'),
 ('Aldridge-Brownhills', 'Aldridge-Brownhills'),
 ('Altrincham and Sale West', 'Altrincham and Sale West'),
 ('Alyn and Deeside', 'Alyn and Deeside'),
 ('Amber Valley', 'Amber Valley')]

In [14]:
dfpt['electorate']= list(dfe['electorate'])
dfpt.head()

name   ons_code                  mp  signature_count  \
42             Aberavon  W07000049  Stephen Kinnock MP              779   
43            Aberconwy  W07000058        Guto Bebb MP             1399   
16       Aberdeen North  S14000001  Kirsty Blackman MP             2137   
25       Aberdeen South  S14000002     Ross Thomson MP             2727   
355  Airdrie and Shotts  S14000003        Neil Gray MP             1198   

     electorate  
42        49821  
43        45525  
16        67745  
25        68056  
355       66792

Read the England, Wales and Scotland constituency shapefile downloaded from [https://github.com/TTitcombe/ConstituencyMap/tree/master/data/boundaries](https://github.com/TTitcombe/ConstituencyMap/tree/master/data/boundaries):

In [15]:
gdf = gpd.read_file(f"UK-constituency/uk_generalized_2015.shp", encoding='utf-8')
gdf.head()

objectid   pcon15cd                  pcon15nm    st_areasha     st_lengths  \
0         1  E14000530                 Aldershot  5.297815e+07   42197.629271   
1         2  E14000531       Aldridge-Brownhills  4.401654e+07   38590.183714   
2         3  E14000532  Altrincham and Sale West  5.092937e+07   47813.461413   
3         4  E14000533              Amber Valley  1.246464e+08   64665.130033   
4         5  E14000534   Arundel and South Downs  6.452509e+08  333618.028722   

                                            geometry  
0  POLYGON ((-0.7754662421455992 51.3319588757355...  
1  POLYGON ((-1.905083771468352 52.64320757091168...  
2  POLYGON ((-2.315991936682887 53.43467382108594...  
3  POLYGON ((-1.33163551111198 53.08098788875827,...  
4  (POLYGON ((-0.5626196767013031 51.055736723659...

In [16]:
len(gdf)

632

gdf has less rows than  the previous two dataframes, that contain the Ireland data, too.

Extract from the dataframe `dfpt` the rows whose string in `'name'`  column is present in `gdf['pcon15nm']`, too. 

In [17]:
gdf_names = list(gdf['pcon15nm'])

dfptn = dfpt[dfpt['name'].isin(gdf_names)] 
dfptn =  dfptn.reset_index(drop=True) 
dfptn.head()

name   ons_code                  mp  signature_count  \
0            Aberavon  W07000049  Stephen Kinnock MP              779   
1           Aberconwy  W07000058        Guto Bebb MP             1399   
2      Aberdeen North  S14000001  Kirsty Blackman MP             2137   
3      Aberdeen South  S14000002     Ross Thomson MP             2727   
4  Airdrie and Shotts  S14000003        Neil Gray MP             1198   

   electorate  
0       49821  
1       45525  
2       67745  
3       68056  
4       66792

In [18]:
len(dfptn)

630

Set up the list of indexes in gdf that will be used to colormap the coresponding geometry:

In [19]:
choro_id = [gdf_names.index(cname) for cname in dfptn['name'] if cname in gdf_names]
print(len(choro_id))
dfptn['choro_id'] = choro_id
assert len(choro_id) == len(dfptn)

630


True

In [22]:
dfptn.sort_values(['choro_id'], inplace=True)
dfptn.head()

name   ons_code                      mp  \
5                  Aldershot  E14000530         Leo Docherty MP   
6        Aldridge-Brownhills  E14000531         Wendy Morton MP   
7   Altrincham and Sale West  E14000532     Sir Graham Brady MP   
9               Amber Valley  E14000533          Nigel Mills MP   
13   Arundel and South Downs  E14000534  Rt Hon Nick Herbert MP   

    signature_count  electorate  choro_id  
5              1808       72430         0  
6               783       60215         1  
7              3383       71511         2  
9              1117       69510         3  
13             3573       77242         4

Compute the percent of electorate in each constituency that signed the petition:

In [23]:
percent_signed = [round(signed*100/el, 2) for signed, el in zip(dfptn['signature_count'], dfptn['electorate'])]

Function to map a val to a  Plotly rgb-colorscale:

In [24]:
from ast import literal_eval
def get_color_for_val(val, vmin, vmax, pl_colorscale):
    if pl_colorscale[0][1][:3] != 'rgb':
        raise ValueError('This function works only with Plotly type rgb-colorscales')
    if vmin >= vmax:
        raise ValueError('vmin should be < vmax')
        
    plotly_scale, plotly_colors = (list(map(float, np.array(pl_colorscale)[:,0])), 
                                   np.array(pl_colorscale)[:,1]) 
    colors_01=np.array(list(map(literal_eval,[color[3:] for color in plotly_colors] )))/255.   #color codes in [0,1]
    
    v= (val - vmin) / float((vmax - vmin)) # val is mapped to v in [0,1]
    #find two consecutive values in plotly_scale such that   v is in  the corresponding interval
    idx = 0
   
    while(v > plotly_scale[idx+1]): 
        idx += 1  
    left_scale_val = plotly_scale[idx]
    right_scale_val = plotly_scale[idx+ 1]
    vv = (v - left_scale_val) / (right_scale_val - left_scale_val)
    #get   [0,1]-valued color code representing the rgb color corresponding to val
    val_color01 = colors_01[idx] + vv * (colors_01[idx + 1] - colors_01[idx])
    val_color_0255 = list(map(np.uint8, 255*val_color01+0.5))
    return f'rgb{str(tuple(val_color_0255))}'

Colorscale definition:

In [25]:
deep = [[0.0, 'rgb(253, 253, 204)'],
 [0.1, 'rgb(201, 235, 177)'],
 [0.2, 'rgb(145, 216, 163)'],
 [0.3, 'rgb(102, 194, 163)'],
 [0.4, 'rgb(81, 168, 162)'],
 [0.5, 'rgb(72, 141, 157)'],
 [0.6, 'rgb(64, 117, 152)'],
 [0.7, 'rgb(61, 90, 146)'],
 [0.8, 'rgb(65, 64, 123)'],
 [0.9, 'rgb(55, 44, 80)'],
 [1.0, 'rgb(39, 26, 44)']]

In [27]:
def get_choropleth_data(gdf, index_list, zvals, customdata, tolerance=0.025,
                         colorscale=deep,   linewidth=0.5, 
                        linecolor= 'rgb(245, 245, 245)', colorbar=True):  
    # gdf - geopandas dataframe containing at least the geometry column 
    # index_list - a sublist of list(gdf.index) for the  geometries to be plotted; gdf.index for all data in gdf
    # zvals - list of values associated to each geometry, to be mapped to the colorscale
    # customdata - an array of data to be passed to hovertemplate
    # tolerance - float parameter to set the Polygon/MultiPolygon degree of simplification
    # colorscale - a  rgb colorscale explicitly defined, not a Plotly coloscale name given as string, such as 'Viridis'
    # linecolor - color code for region/county boundary line
    # returns len(index_list) traces for filled regions, plus the centroids trace, and optionally a dummy trace for colorbar
    
    cdata = []
    x_centroids = []
    y_centroids = []
    centro_tooltip = []
    vmin, vmax = np.array(zvals).min(), np.array(zvals).max()
   
    
    for k, index in enumerate(index_list):
        geo = gdf['geometry'][index].simplify(tolerance)
        xb = []
        yb = []
        c_x, c_y = geo.centroid.xy
        if isinstance(geo.boundary, LineString):
            xc, yc = geo.boundary.coords.xy
            xb.extend(xc.tolist()+[None])
            yb.extend(yc.tolist()+ [None])
        elif  isinstance(geo.boundary, MultiLineString): 
            for b in geo.boundary:
                xc, yc = b.coords.xy
                xb.extend(xc.tolist()+[None])
                yb.extend(yc.tolist()+ [None])
        else:
            raise ValueError('Unknown boundary type')
            
        x_centroids.extend(list(c_x))
        y_centroids.extend(list(c_y))
       
        color = get_color_for_val(zvals[k], vmin, vmax, colorscale) 
       
        
        region = go.Scatter(# choropleth trace
                            showlegend = False,
                            mode='lines',
                            line = dict(color=linecolor, width=linewidth),
                            x=list(xb),
                            y=list(yb),
                            fill='toself',
                            fillcolor = color,
                            hoverinfo='none')
        
        cdata.append(region)
        
    #define the trace for geometry centers
    centroids = go.Scatter(
                     mode='markers',
                     showlegend=False,
                     customdata=customdata,
                     marker = dict(size=6, color='white', opacity=0.1),
                     x=x_centroids,
                     y=y_centroids,
                     hovertemplate =  "<b>Constituency</b>:"+
                                      "<br>%{customdata[0]}<br>" +
                                      "<b>%{customdata[1]}</b>" +
                                      "<br><b>Signatures</b>: %{customdata[2]}"+
                                      "<br>%{customdata[4]}% from %{customdata[3]} constituents",
                             
                     name=''
                    )  
    if colorbar:
        dummy_tr = go.Scatter(
                        x=[xb[0], xb[0]],
                        y=[yb[0], yb[0]],
                        showlegend=False, 
                        mode='markers',
                        name='',
                        marker=dict(size=0, color=[vmin, vmax], colorscale=colorscale,
                                colorbar=dict(thickness=20, ticklen=4, x =-0.12)),
                        hoverinfo='none')
    
        cdata.extend([centroids, dummy_tr]) 
    else:
        cdata.append(centroids)
    return cdata

Define customdata to be used in a hovertemplate definition:

In [28]:
customdata = dfptn[['name', 'mp', 'signature_count', 'electorate']].values
customdata = np.vstack((customdata.T, percent_signed)).T

In [29]:
data = get_choropleth_data(gdf, 
                           list(dfptn['choro_id']), 
                           percent_signed, 
                           customdata,
                           linecolor='rgb(100,100,100)')

In [30]:
axis_style = dict(visible=False)
title = f'Petition "Do not prorogue Parliament". {signatures:,} signatures' 

layout = dict(title_text=title,
              title_x=0.5,
              font=dict(family='Balto', size=14),
              xaxis = dict(axis_style),
              yaxis = dict(axis_style),
              width = 590,
              height = 820,
              margin =dict(r =5),
              hovermode='closest',
              plot_bgcolor="#E5ECF6",
              paper_bgcolor="#E5ECF6",
              images=[dict(
                        source="https://www.dw.com/image/49741008_303.jpg",
                        xref="paper", yref="paper",
                        x=1.1, y=0.55,
                        sizex=0.47, sizey=0.5,
                        xanchor="right", yanchor="bottom"
                    )])

In [31]:
fig = go.Figure(data=data, layout=layout)
fig.show()

Note:  Except for the constituency shapefile, all other data are read from an URL. Hence downloading the shapefile from the mentioned URL, and running this notebook you can get an updated choropleth  if meanwhile more signatures were done.
    

September 1, 2019, 21:16:00
